In [ ]:
!pip install resampy
import os
import librosa
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.utils import shuffle
from keras.utils import to_categorical
from keras.models import Sequential
from keras.layers import Dense, Dropout
from sklearn.metrics import confusion_matrix, classification_report

# Define the path to the UrbanSound8K and gunshot audio datasets
urban_sound_path = "/kaggle/input/urbansound8k/"
gunshot_audio_path = "/kaggle/input/gunshot-audio-dataset/"

# Preprocess the UrbanSound8K audio files
def preprocess_urbansound_audio(audio_path):
    features = []
    labels = []
    # Iterate over the subdirectories in the main directory
    for folder in os.listdir(audio_path):
        folder_path = os.path.join(audio_path, folder)
        # Check if the current item is a directory
        if os.path.isdir(folder_path):
            # Iterate over the files in the subdirectory
            for filename in os.listdir(folder_path):
                file_path = os.path.join(folder_path, filename)
                # Load audio file
                audiodata, sample_rate = librosa.load(file_path, res_type='kaiser_fast')
                # Extract features
                mels = np.mean(librosa.feature.melspectrogram(y=audiodata, sr=sample_rate).T, axis=0)
                features.append(mels)
                labels.append(0)  # Set label as 0 for non-gunshot
    return features, labels



# Preprocess the gunshot audio files
def preprocess_gunshot_audio(audio_path):
    features = []
    labels = []
    for folder in os.listdir(audio_path):
        folder_path = os.path.join(audio_path, folder)
        for filename in os.listdir(folder_path):
            file_path = os.path.join(folder_path, filename)
            # Load audio file
            audiodata, sample_rate = librosa.load(file_path, res_type='kaiser_fast')
            # Extract features
            mels = np.mean(librosa.feature.melspectrogram(y=audiodata, sr=sample_rate).T, axis=0)
            features.append(mels)
            labels.append(1)  # Set label as 1 for gunshot
    return features, labels

# Preprocess both datasets
urban_sound_features, urban_sound_labels = preprocess_urbansound_audio(urban_sound_path)
gunshot_features, gunshot_labels = preprocess_gunshot_audio(gunshot_audio_path)

# Concatenate features and labels from both datasets
X = np.concatenate((urban_sound_features, gunshot_features), axis=0)
Y = np.concatenate((urban_sound_labels, gunshot_labels), axis=0)

# Convert labels to categorical
Y = to_categorical(Y, num_classes=2)  # Assuming binary classification (gunshot or non-gunshot)

# Shuffle the data
X, Y = shuffle(X, Y, random_state=42)

# Split the data into training and testing sets
X_train, X_test, Y_train, Y_test = train_test_split(X, Y, random_state=123, test_size=0.2)

# Define the model
model = Sequential([
    Dense(1000, activation='relu', input_shape=(128,)),
    Dropout(0.5),
    Dense(500, activation='relu'),
    Dropout(0.5),
    Dense(2, activation='softmax')  # Output layer with 2 units for binary classification
])

# Compile the model
model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])

# Train the model
history = model.fit(X_train, Y_train, epochs=50, batch_size=32, validation_data=(X_test, Y_test))

# Evaluate the model
loss, accuracy = model.evaluate(X_test, Y_test)
print("Test Loss:", loss)
print("Test Accuracy:", accuracy)

# Predictions
Y_pred = model.predict(X_test)
y_pred = np.argmax(Y_pred, axis=1)

# Classification Report
print(classification_report(np.argmax(Y_test, axis=1), y_pred))

# Confusion Matrix
conf_matrix = confusion_matrix(np.argmax(Y_test, axis=1), y_pred)
print("Confusion Matrix:")
print(conf_matrix)
model.save("gunshot_detection_model.h5")

# Function to predict class of audio file
def prediction_parser(filename, model):
    # Load audio data
    audiodata, sample_rate = librosa.load(filename, res_type='kaiser_fast') 
    # Extract melspectrogram feature
    mels = np.mean(librosa.feature.melspectrogram(y=audiodata, sr=sample_rate).T, axis=0)
    # Reshape data for prediction
    X = mels.reshape(1, -1)
    # Predict the class
    class_id = np.argmax(model.predict(X))
    if class_id == 1:
        print('It is a gunshot.')
    else:
        print('It is a non-gunshot sound.')
    # Play the audio
    return Audio(data=audiodata, rate=sample_rate)




In [6]:
from IPython.display import Audio

# Test the model with a gunshot sound file
gunshot_file_path = '/kaggle/input/trial4/Drivebyshooting.wav'
prediction_parser(gunshot_file_path, new_model)

1/1 [==============================] - 0s 43ms/step
It is a gunshot.


In [1]:
!pip install resampy
import os
import librosa
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.utils import shuffle
from keras.utils import to_categorical
from keras.models import Sequential
from keras.layers import Dense, Dropout
from sklearn.metrics import confusion_matrix, classification_report
from keras.models import load_model

# Load the saved model from another location
loaded_model = load_model("/kaggle/input/trainedmodel1/gunshot_detection_model.h5")
new_model = load_model("/kaggle/input/trainedmodel2/updated_gunshot_detection_model.h5")

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 10.7 MB/s eta 0:00:0000:0100:01


/opt/conda/lib/python3.10/site-packages/scipy/__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.23.5
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


In [2]:
def prediction_parser(filename, model):
    # Load audio data
    audiodata, sample_rate = librosa.load(filename, res_type='kaiser_fast') 
    # Extract melspectrogram feature
    mels = np.mean(librosa.feature.melspectrogram(y=audiodata, sr=sample_rate).T, axis=0)
    # Reshape data for prediction
    X = mels.reshape(1, -1)
    # Predict the class
    class_id = np.argmax(model.predict(X))
    if class_id == 1:
        print('It is a gunshot.')
    else:
        print('It is a non-gunshot sound.')
    # Play the audio
    return Audio(data=audiodata, rate=sample_rate)

In [29]:
import librosa
import numpy as np
from keras.models import load_model
from keras.utils import to_categorical

# Load the pre-trained model
model = load_model("/kaggle/input/trainedmodel1/gunshot_detection_model.h5")

# Function to preprocess the new audio file
def preprocess_audio(audio_file_path):
    # Load audio data
    audiodata, sample_rate = librosa.load(audio_file_path, res_type='kaiser_fast')
    
    # Extract mel spectrogram feature
    mels = np.mean(librosa.feature.melspectrogram(y=audiodata, sr=sample_rate).T, axis=0)
    
    return mels

# Path to the new audio file
new_audio_file_path = "/kaggle/input/gopro-shooting/GoPro Shooting Guns Compilation.wav"

# Preprocess the new audio file
new_audio_features = preprocess_audio(new_audio_file_path)

# Label the new audio file as a gunshot
new_audio_label = 1  # Gunshot label

# Convert features and label to numpy arrays
X = np.array([new_audio_features])
Y = np.array([[new_audio_label]])

# Convert labels to categorical
Y = to_categorical(Y, num_classes=2)  # Assuming binary classification (gunshot or non-gunshot)

# Retrain the model using the new data
history = model.fit(X, Y, epochs=50, batch_size=32)

# Save the updated model
model.save("updated_gunshot_detection_model.h5")


Epoch 1/50
1/1 [==============================] - 1s 563ms/step - loss: 1.1783 - accuracy: 0.0000e+00
Epoch 2/50
1/1 [==============================] - 0s 17ms/step - loss: 1.4992 - accuracy: 0.0000e+00
Epoch 3/50
1/1 [==============================] - 0s 14ms/step - loss: 1.3856 - accuracy: 0.0000e+00
Epoch 4/50
1/1 [==============================] - 0s 14ms/step - loss: 2.2649 - accuracy: 0.0000e+00
Epoch 5/50
1/1 [==============================] - 0s 11ms/step - loss: 0.7061 - accuracy: 0.0000e+00
Epoch 6/50
1/1 [==============================] - 0s 15ms/step - loss: 0.9406 - accuracy: 0.0000e+00
Epoch 7/50
1/1 [==============================] - 0s 13ms/step - loss: 0.9729 - accuracy: 0.0000e+00
Epoch 8/50
1/1 [==============================] - 0s 17ms/step - loss: 0.4197 - accuracy: 1.0000
Epoch 9/50
1/1 [==============================] - 0s 14ms/step - loss: 0.1068 - accuracy: 1.0000
Epoch 10/50
1/1 [==============================] - 0s 13ms/step - loss: 0.4744 - accuracy: 1.0000


SyntaxError: invalid syntax (1186651998.py, line 1)